In [1]:
!pip install pycairo

In [2]:
pip install igraph

Note: you may need to restart the kernel to use updated packages.


In [3]:
import igraph as ig
import numpy as np
import os
import json
import pandas as pd 
import csv
import math
from igraph import Graph, plot

In [4]:
df = pd.read_csv("..\Jupyter Notebook\COVID19Dataset\metadata.csv", low_memory=False)

In [5]:
#Criação de uma variável auxiliar que pega o dado que interessa do csv importado e não pega os valores nulos desse campo
df_notna_aux1 = df[df['abstract'].notna()]

#Da váriavel auxiliar anterior pega os autores
df_notna_aux2 = df_notna_aux1[df_notna_aux1['authors'].notna()]

#Da anterior pega a data de publicação
df_notna_aux3 = df_notna_aux2[df_notna_aux2['publish_time'].notna()]

#Da anterior pega o arquivo json 
#df_notna = df_notna_aux3[df_notna_aux2['pdf_json_files'].notna()]
df_notna = df_notna_aux3.loc[df_notna_aux2['pdf_json_files'].notna()]

#Converte o formato de plublish_time 
#df_notna['publish_time'] = pd.to_datetime(df_notna['publish_time'])
df_notna = df_notna.copy()
df_notna.loc[:, 'publish_time'] = pd.to_datetime(df_notna['publish_time'], errors='coerce').copy()

#filtra o ano de 2020 somente
df_ano = df_notna[(df_notna['publish_time'] >= '2020-01-01 00:00:00') & (df_notna['publish_time'] <= '2023-01-01 00:00:00')]

#filtro com os nomes de pelo menos uma das vacinas
df_vacina = df_ano.loc[df_notna['abstract'].str.contains("Coronavac", case=False)]

df_finalizado = df_vacina[df_vacina['title'].notna()]

print("Número de artigos DFFinalizado: ",len(df_finalizado))
print("Número de artigos DFNotNA: ",len(df_notna))

C:\Users\sarah\AppData\Local\Temp\ipykernel_8264\3748943549.py:17: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  df_notna.loc[:, 'publish_time'] = pd.to_datetime(df_notna['publish_time'], errors='coerce').copy()


Número de artigos DFFinalizado:  295
Número de artigos DFNotNA:  325855


In [6]:
#Aqui é feita a união de caminho de diretório de forma portável, 
#armazenando os caminhos completos em uma lista
datafiles = []
for filename in df_finalizado['pdf_json_files']:
    ifile = os.path.join('..\Jupyter Notebook\COVID19Dataset', filename)
    datafiles.append(ifile)
    
with open(datafiles[0],'r')as f:
    doc = json.load(f)

In [7]:
citbib = []

for file in datafiles:
    try:
        with open(file, 'r') as f:
            doc = json.load(f)
        
        id = doc['paper_id']
        title = doc['metadata']['title']
        
        authors_doc = []
        for author in doc['metadata']['authors']:
            first = author['first']
            middle = author.get('middle', None)
            last = author['last']
            suffix = author.get('suffix', None)
            
            affiliation = author.get('affiliation', {})
            laboratory = affiliation.get('laboratory', None)
            institution = affiliation.get('institution', None)
            
            location = affiliation.get('location', {})
            settlement = location.get('settlement', None)
            region = location.get('region', None)
            country = location.get('country', None)
            
            email = author.get('email', None)
            
            authors_doc.append({
                'first': first,
                'middle': middle,
                'last': last,
                'suffix': suffix,
                'affiliation': {
                    'laboratory': laboratory,
                    'institution': institution,
                    'location': {
                        'settlement': settlement,
                        'region': region,
                        'country': country
                    }
                },
                'email': email
            })
        
        bibEntries = []
        for key, value in doc['bib_entries'].items():
            refid = key
            bib_title = value['title']
            
            authors_bib = []
            for author in value['authors']:
                first = author['first']
                middle = author.get('middle', None)
                last = author['last']
                suffix = author.get('suffix', None)
                
                authors_bib.append({
                    'first': first,
                    'middle': middle,
                    'last': last,
                    'suffix': suffix
                })
            
            year = value['year']
            
            try:
                DOI = value['other_ids']['DOI'][0]
            except KeyError:
                DOI = np.nan
            
            bibEntries.append({
                'refid_bib': refid,
                'title': bib_title,
                'authors_bib': authors_bib,
                'year': year,
                'DOI': DOI
            })
        
        citbib.append({
            'id': id,
            'title': title,
            'authors_doc': authors_doc,
            'bib': bibEntries
        })
    except:
        pass


In [8]:
#salvando em um csv
# transformar citbib em DataFrame
df = pd.DataFrame(citbib)

# salvar em um arquivo CSV
df.to_csv('citbib.csv', index=False)

In [9]:
title_to_id = {}
connections = []

# Mapear cada title para um id genérico
def get_id_for_title(title):
    if title not in title_to_id:
        id = len(title_to_id) + 1
        title_to_id[title] = id
    return title_to_id[title]

# Percorrer 'citbib' e 'bib' para mapear os títulos
for item in citbib:
    title = item['title']
    _ = get_id_for_title(title)
    
    bib_entries = item['bib']
    for entry in bib_entries:
        bib_title = entry['title']
        _ = get_id_for_title(bib_title)

# Armazenar os mapeamentos de título para ID em um arquivo CSV
with open('mapeamentos.csv', 'w', newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['id', 'title'])  # Cabeçalho do arquivo
    
    for title, id in title_to_id.items():
        writer.writerow([id, title])

# Verificar as conexões entre os títulos
for item in citbib:
    doc_id = get_id_for_title(item['title'])
    bib_entries = item['bib']
    
    for entry in bib_entries:
        refid_bib = entry['refid_bib']
        
        if refid_bib in title_to_id:
            cited_id = title_to_id[refid_bib]
            connection = (doc_id, item['title'], cited_id, refid_bib)
            
            if connection not in connections:
                connections.append(connection)

# Armazenar as conexões em um arquivo CSV
with open('conexoes.csv', 'w', newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['id1', 'title1', 'id2', 'title2'])  # Cabeçalho do arquivo
    
    for connection in connections:
        writer.writerow(connection)

In [10]:
title_to_id = {}
unique_titles = set()

# Percorrer 'citbib' e 'bib' para mapear os títulos para seus IDs genéricos
for item in citbib:
    title = item['title']
    unique_titles.add(title)

    bib_entries = item['bib']
    for entry in bib_entries:
        bib_title = entry['title']
        unique_titles.add(bib_title)

# Armazenar os mapeamentos de título para ID em um arquivo CSV, incluindo apenas os títulos únicos
with open('mapeamentos.csv', 'w', newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['id', 'title'])  # Cabeçalho do arquivo

    for id, title in enumerate(unique_titles, start=1):
        writer.writerow([id, title])
        title_to_id[title] = id

In [11]:
# Dicionário para mapear títulos para IDs genéricos
title_to_id = {}

# Percorrer 'mapeamentos.csv' para obter os mapeamentos de títulos para IDs genéricos
with open('mapeamentos.csv', 'r', newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    next(reader)  # Ignorar o cabeçalho
    
    for row in reader:
        id = int(row[0])
        title = row[1]
        title_to_id[title] = id

# Dicionário para armazenar as relações entre os artigos e os artigos citados
relations = {}

# Percorrer 'citbib' para obter as relações entre os artigos e os artigos citados
for item in citbib:
    doc_id = title_to_id.get(item['title'], None)
    bib_entries = item['bib']
    
    for entry in bib_entries:
        bib_title = entry['title']
        
        if bib_title in title_to_id:
            cited_id = title_to_id[bib_title]
            
            # Evitar repetições de combinações
            if (doc_id, cited_id) not in relations and doc_id != cited_id:
                relations[(doc_id, cited_id)] = (item['title'], bib_title)

# Armazenar as relações em um novo arquivo CSV
with open('relacoes.csv', 'w', newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(['id1', 'artigotitle1', 'id2', 'artigotitle2'])  # Cabeçalho do arquivo
    
    for (doc_id, cited_id), (doc_title, cited_title) in relations.items():
        writer.writerow([doc_id, doc_title, cited_id, cited_title])


In [12]:
relations = []
with open('relacoes.csv', 'r', newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    next(reader)  # Pular o cabeçalho
    for row in reader:
        id1, artigotitle1, id2, artigotitle2 = row
        relations.append((id1, id2))

all_ids = set()
for id1, id2 in relations:
    all_ids.add(id1)
    all_ids.add(id2)

g = ig.Graph(directed=False)

for node_id in all_ids:
    g.add_vertex(name=node_id)

for id1, id2 in relations:
    g.add_edge(id1, id2)
    
layout = g.layout_fruchterman_reingold()

ig.plot(g, layout=layout)

In [13]:
relations = []
with open('relacoes.csv', 'r', newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    next(reader)  # Pular o cabeçalho
    for row in reader:
        id1, artigotitle1, id2, artigotitle2 = row
        relations.append((id1, artigotitle1, id2, artigotitle2))

# Criar um conjunto para todos os IDs
all_ids = set()
for id1, _, id2, _ in relations:
    all_ids.add(id1)
    all_ids.add(id2)

# Criar um dicionário para mapear IDs a títulos
id_to_title = {}
for id1, title1, id2, title2 in relations:
    id_to_title[id1] = title1
    id_to_title[id2] = title2
    
dict(list(id_to_title.items())[:3])

{'3883': 'Heterologous prime-boost strategies for COVID-19 vaccines',
 '1659': 'Draft landscape and tracker of COVID-19 candidate vaccines. World Health Organization',
 '4523': 'COVID-19: vaccine brands can be mixed in "extremely rare occasions," says Public Health England'}

In [ ]:
gCitacoes = ig.Graph(directed=False)

# Adicionar nós ao grafo e definir rótulos
for node_id in all_ids:
    gCitacoes.add_vertex(name=node_id)  # Crie os nós com os IDs como nomes

# Definir rótulos dos nós com os títulos correspondentes
for id1, title1, id2, title2 in relations:
    gCitacoes.vs.find(name=id1)['label'] = title1
    gCitacoes.vs.find(name=id2)['label'] = title2

# Adicionar arestas ao grafo
for id1, _, id2, _ in relations:
    if id1 != id2:
        gCitacoes.add_edge(id1, id2)

# Plotar o grafo
layout = gCitacoes.layout_fruchterman_reingold()
ig.plot(gCitacoes, layout=layout)

In [ ]:
graph = Graph(directed=False)

# Leitura do arquivo 'relacoes.csv'
with open('relacoes.csv', 'r', newline='', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    next(reader)  # Ignorar o cabeçalho

    for row in reader:
        doc_id1, doc_title1, doc_id2, doc_title2 = row
        graph.add_vertex(doc_id1, label=doc_title1)  # Adicionar nó 1
        graph.add_vertex(doc_id2, label=doc_title2)  # Adicionar nó 2
        graph.add_edge(doc_id1, doc_id2)  # Adicionar aresta entre os nós

layout = graph.layout_fruchterman_reingold()
ig.plot(graph, layout=layout)

In [15]:
#Converte igraph para json no formato simajs
class NpEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.integer):
            return int(obj)
        if isinstance(obj, np.floating):
            return float(obj)
        if isinstance(obj, np.ndarray):
            return obj.tolist()
        return super(NpEncoder, self).default(obj)

def ig_to_json(graph, path):
    assert isinstance(graph, ig.Graph)
    nodes = []
    edges = []

    if not 'layout' in graph.attributes():
        graph['layout'] = graph.layout_auto()

    for v, coords in zip(graph.vs, graph['layout']):
        v_id = str(v.index)
        v_attributes = v.attributes()
        v_label = v_attributes.pop('label', None)
        if not v_label:
            v_label = v_id
        v_size = v_attributes.pop('size', None)
        if v_size:
            v_size = float(v_size)
        v_x = coords[0]
        v_y = coords[1]
        node = dict(key=v_id, attributes={**v_attributes,
            **dict(label=v_label, size=v_size, x=v_x, y=v_y)})
        nodes.append(node)

    for e in graph.es:
        e_id = str(e.index)
        e_source = str(e.source)
        e_target = str(e.target)
        e_attributes = e.attributes()
        e_size = e_attributes.pop('size', None)
        if e_size:
            e_size = float(e_size)
        edge = dict(key=e_id, source=e_source, target=e_target, attributes={**e_attributes,
            **dict(size=e_size)})
        edges.append(edge)

    data = dict(nodes=nodes, edges=edges)
    with open(path, 'w') as f:
        json.dump(data, f, ensure_ascii=False, cls=NpEncoder)
    return os.path.exists(path)

In [15]:
# Obtém o caminho absoluto do diretório atual
current_dir = os.getcwd()

# Constrói o caminho completo para o arquivo JSON
json_path = os.path.join(current_dir, 'RedeCitacaoSemDefinirRotulodoNo.json')

# Chama a função ig_to_json passando o caminho completo
ig_to_json(g, json_path)

True